In [ ]:
#@title Step 1: Installing and Importing Necessary Libraries
# We are installing the necessary libraries in the Google Colab environment.
# yfinance: To fetch financial data from Yahoo Finance.
# tensorflow: To build and train the neural network.
# scikit-learn: For data preprocessing (normalization).
!pip install yfinance tensorflow scikit-learn pandas matplotlib -q

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import yfinance as yf
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout
import datetime

print("Libraries have been successfully installed and imported!")


#@title Step 2: Fetching and Visualizing Bitcoin Data
# Let's fetch the BTC-USD (Bitcoin/US Dollar) data for the last few years.
start_date = '2019-01-01'
# We set the end date to today's date.
end_date = datetime.date.today().strftime("%Y-%m-%d")

try:
    btc_data = yf.download('BTC-USD', start=start_date, end=end_date)
    print(f"Bitcoin data between {start_date} and {end_date} has been fetched.")
    print("First 5 rows of the dataset:")
    print(btc_data.head())

    # Let's plot the 'Close' prices of the dataset in a graph.
    plt.figure(figsize=(14, 7))
    plt.style.use('seaborn-v0_8-darkgrid')
    plt.plot(btc_data['Close'], color='orange')
    plt.title('Bitcoin Closing Prices (BTC-USD)', fontsize=16)
    plt.xlabel('Date', fontsize=12)
    plt.ylabel('Price (USD)', fontsize=12)
    plt.legend(['Closing Price'])
    plt.show()

except Exception as e:
    print(f"An error occurred while fetching data: {e}")


#@title Step 3: Data Preprocessing
# We are preparing the data to train our model.

# We will only use the 'Close' column.
close_data = btc_data['Close'].values.reshape(-1, 1)

# We are scaling the data between 0 and 1 (Normalization).
# Neural networks work more efficiently with data in this range.
scaler = MinMaxScaler(feature_range=(0, 1))
scaled_data = scaler.fit_transform(close_data)

# We are splitting the dataset: 80% for training, 20% for testing.
training_data_len = int(np.ceil(len(scaled_data) * 0.8))

# Let's create the training data.
train_data = scaled_data[0:int(training_data_len), :]

# Let's prepare the x_train and y_train sets for training.
# The model will predict the next day's price by looking at the past 60 days' prices.
prediction_days = 60
x_train = []
y_train = []

for i in range(prediction_days, len(train_data)):
    x_train.append(train_data[i-prediction_days:i, 0])
    y_train.append(train_data[i, 0])

# Converting the lists to numpy arrays.
x_train, y_train = np.array(x_train), np.array(y_train)

# Reshaping the data into a 3D format suitable for the LSTM model: [number of samples, time steps, number of features]
x_train = np.reshape(x_train, (x_train.shape[0], x_train.shape[1], 1))
print(f"Training data prepared. x_train shape: {x_train.shape}")


#@title Step 4: Building the LSTM Model
# We are designing our neural network model using Keras.

model = Sequential()

# Layer 1: LSTM layer with 50 neurons. `return_sequences=True` because we will send data to the next LSTM layer.
model.add(LSTM(units=50, return_sequences=True, input_shape=(x_train.shape[1], 1)))
model.add(Dropout(0.2)) # We are deactivating 20% of the neurons to prevent overfitting.

# Layer 2: LSTM layer with 50 neurons.
model.add(LSTM(units=50, return_sequences=False))
model.add(Dropout(0.2))

# Output Layer: Consists of 1 neuron as we will predict a single value (the price).
model.add(Dense(units=1))

# Compiling the model. 'adam' is a popular optimizer. 'mean_squared_error' is the loss function.
model.compile(optimizer='adam', loss='mean_squared_error')

# Let's see the model's architecture.
model.summary()


#@title Step 5: Training the Model
# We are training the model with the prepared data.
# epochs: The number of times the model will process the entire dataset.
# batch_size: The number of data samples the model will see in each iteration.
print("Starting model training...")
history = model.fit(x_train, y_train, batch_size=32, epochs=25)
print("Model training completed!")


#@title Step 6: Testing the Model and Evaluating Results
# Let's create the test data.
test_data = scaled_data[training_data_len - prediction_days:, :]

# Let's prepare the x_test and y_test sets.
x_test = []
y_test = close_data[training_data_len:, :] # y_test is the original (unscaled) data.

for i in range(prediction_days, len(test_data)):
    x_test.append(test_data[i-prediction_days:i, 0])

x_test = np.array(x_test)
x_test = np.reshape(x_test, (x_test.shape[0], x_test.shape[1], 1))

# Let's make predictions on the test data with the model.
predictions = model.predict(x_test)

# Let's scale the predictions back to the original price (from 0-1 range to USD).
predictions = scaler.inverse_transform(predictions)

# Let's calculate RMSE (Root Mean Squared Error) to measure the model's performance.
rmse = np.sqrt(np.mean(((predictions - y_test) ** 2)))
print(f'\nModel Error Rate on Test Data (RMSE): {rmse:.2f} USD')

# Let's show the actual and predicted prices on the same graph.
train = btc_data[:training_data_len]
valid = btc_data[training_data_len:].copy() # Using .copy() to avoid SettingWithCopyWarning.
valid.loc[:, 'Predictions'] = predictions

plt.figure(figsize=(16, 8))
plt.title('Model Predictions vs Actual Prices', fontsize=16)
plt.xlabel('Date', fontsize=12)
plt.ylabel('Closing Price (USD)', fontsize=12)
plt.plot(train['Close'], color='blue', alpha=0.6)
plt.plot(valid['Close'], color='green')
plt.plot(valid['Predictions'], color='red', linestyle='--')
plt.legend(['Training Data', 'Actual Price', 'Predicted Price'], loc='upper left')
plt.show()

# Let's take a closer look at the last 15 days of predictions.
print("\nLast 15 Days of Actual and Predicted Prices:")
print(valid[['Close', 'Predictions']].tail(15))


#@title Step 7: Using the Model to Predict the Future

# Get the last 60 days of data
last_60_days = scaled_data[-prediction_days:]
X_predict = np.reshape(last_60_days, (1, prediction_days, 1))

# Make a guess
predicted_price_scaled = model.predict(X_predict)
predicted_price = scaler.inverse_transform(predicted_price_scaled)

# Date information
tomorrow = datetime.date.today() + datetime.timedelta(days=1)

# Convert with float() to avoid errors
last_row = btc_data.tail(1)
last_index = last_row.index[0]
last_actual_price = float(last_row['Close'].iloc[0])

# Print results
print("\n" + "="*50)
print("FUTURE PREDICTION")
print("="*50)
print(f"Last closing price({last_index.strftime('%Y-%m-%d')}): {last_actual_price:.2f} USD")
print(f"The model {tomorrow.strftime('%Y-%m-%d')} Bitcoin price prediction for: {float(predicted_price[0][0]):.2f} USD")
print("="*50)
print("\nWARNING: This model is for educational purposes only and does not constitute financial advice.")


